In [1]:
# Import necessary libraries
#!pip install folium
#!pip3 install neo4j-driver

import pandas as pd
import folium # map rendering library
from folium import plugins
import pandas as pd
from neo4j import GraphDatabase, basic_auth

# Read and Map Crime dataset

In [2]:
#Read Excel file into dataframe
muni_geo_df = pd.read_csv('Municipalities_Location_2022.csv', index_col=0)
print(len(muni_geo_df))
muni_geo_df

412


Entidad            Municipio  2022 AVG   Latitude   Longitude
0    Aguascalientes       Aguascalientes   2501.33  21.880487 -102.296719
1    Aguascalientes             Asientos     73.17  22.132107 -102.095256
2    Aguascalientes             Calvillo     82.00  21.849624 -102.712543
3    Aguascalientes          Jesús María    275.00  21.934555 -102.468452
4    Aguascalientes  Pabellón de Arteaga     95.83  22.104933 -102.301624
..              ...                  ...       ...        ...         ...
407       Zacatecas            Fresnillo    405.50  23.224924 -103.016289
408       Zacatecas            Guadalupe    410.00  22.782384 -102.450506
409       Zacatecas                Jerez     94.50  22.710593 -103.001473
410       Zacatecas           Sombrerete     60.50  23.574518 -103.646828
411       Zacatecas            Zacatecas    460.00  22.775389 -102.572271

[412 rows x 5 columns]

In [3]:
# create map of Mexico using latitude and longitude values
map_mexico = folium.Map(location=[25, -102], zoom_start=6)

# add markers to map
for lat, lon, State, Municipality in zip(muni_geo_df['Latitude'], muni_geo_df['Longitude'], muni_geo_df['Entidad'], muni_geo_df['Municipio']):
    label = '{}, {}'.format(State, Municipality)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=1,
        popup=label,
        color='red',
        fill=False,
        fill_opacity = 0.2,
        parse_html=False).add_to(map_mexico)  

heat_data = list(zip(muni_geo_df['Latitude'], muni_geo_df['Longitude'],muni_geo_df['2022 AVG']))
plugins.HeatMap(heat_data, radius=25).add_to(map_mexico)
 
map_mexico

In [4]:
# Test the API with the coordinates from Calgary and Edmonton
route_uri = 'http://router.project-osrm.org/route/v1/driving/'
loc_pair = '-114.065465,51.046095;-113.507996,53.535411'
result = pd.read_json( route_uri + loc_pair,lines=True)
distance = result['routes'][0][0]['distance']
duration = result['routes'][0][0]['duration']
print("The distance is",distance/1000,"Kms and the duration is", round(duration/60,2),"minutes")

The distance is 297.675 Kms and the duration is 214.22 minutes


## Distance Matrix

 From OSRM (Open Source Routing Machine)
 https://github.com/Project-OSRM/osrm-backend/wiki/Server-api

In [5]:
# Create a new dataframe for the Distance Matrix
matrix = pd.DataFrame()
origin = []
destination = []
durations = []
distances = []

# Loop trough cites to fill the Distance Matrix
for i in range(len(muni_geo_df)):
  for j in range(i+1, len(muni_geo_df)):
    origin.append(muni_geo_df['Municipio'][i])
    LatO = muni_geo_df['Latitude'][i]
    LonO = muni_geo_df['Longitude'][i]
    destination.append(muni_geo_df['Municipio'][j])
    LatD = muni_geo_df['Latitude'][j]
    LonD = muni_geo_df['Longitude'][j]
    
    # Location pair of coordinates
    loc_pair = str(LonO) + ',' + str(LatO) + ';' + str(LonD) + ',' + str(LatD)

    #pass the location pairs to the OSRM API, read to json and extract routs and duration
    result = pd.read_json( route_uri + loc_pair,lines=True)
    distance = result['routes'][0][0]['distance']/1000
    duration = result['routes'][0][0]['duration']/60

    #Print results as they are coming
    print('From',muni_geo_df['Municipio'][i],'to',muni_geo_df['Municipio'][j],'is',round(distance,2), 'Kms')
    
    #append result to list
    distances.append(distance)
    durations.append(duration)

matrix['Origin'] = origin
matrix['Destination'] = destination
matrix['Distance'] = distances
matrix['Duration'] = durations

From Aguascalientes to Asientos is 44.18 Kms
From Aguascalientes to Calvillo is 50.82 Kms
From Aguascalientes to Jesús María is 27.43 Kms
From Aguascalientes to Pabellón de Arteaga is 28.02 Kms
From Aguascalientes to Rincón de Romos is 40.72 Kms
From Aguascalientes to San Francisco de los Romo is 21.16 Kms
From Aguascalientes to Ensenada is 2376.13 Kms
From Aguascalientes to Mexicali is 2107.81 Kms
From Aguascalientes to Playas de Rosarito is 2324.33 Kms
From Aguascalientes to San Felipe is 2309.35 Kms
From Aguascalientes to San Quintín is 2557.48 Kms
From Aguascalientes to Tecate is 2269.85 Kms
From Aguascalientes to Tijuana is 2342.25 Kms
From Aguascalientes to Comondú is 3112.73 Kms
From Aguascalientes to La Paz is 3464.32 Kms
From Aguascalientes to Los Cabos is 3634.43 Kms
From Aguascalientes to Mulegé is 2975.41 Kms
From Aguascalientes to Campeche is 1614.0 Kms
From Aguascalientes to Candelaria is 1497.39 Kms
From Aguascalientes to Carmen is 1464.06 Kms
From Aguascalientes to Cham

In [6]:
matrix.head()

Origin          Destination  Distance   Duration
0  Aguascalientes             Asientos   44.1836  49.048333
1  Aguascalientes             Calvillo   50.8171  47.878333
2  Aguascalientes          Jesús María   27.4281  35.316667
3  Aguascalientes  Pabellón de Arteaga   28.0245  27.666667
4  Aguascalientes      Rincón de Romos   40.7220  36.113333

In [7]:
# Export Distance Matrix to CSV File
matrix.to_csv('Mexico_Distance_Matrix.csv')

In [8]:

# Copy Cities and Distance Matrix to Neo4j import directory
!cp Municipalities_Location_2022.csv "..\.Neo4jDesktop\relate-data\dbmss\dbms-c34bd6bc-a4e9-4e5b-9380-12d3745ca45e\import"
!cp Mexico_Distance_Matrix.csv "..\.Neo4jDesktop\relate-data\dbmss\dbms-c34bd6bc-a4e9-4e5b-9380-12d3745ca45e\import"